![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS - módulo V 2019 Violência

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(tictoc)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [ ]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2019>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2019>")

In [ ]:
#Selecionando registros válidos para o módulo U e calculando peso amostral - summary de verificação
pns2019.1<- <Coloque aqui o nome do arquivo RDATA>  %>% filter(V0025A==1) 
pns2019.1<-pns2019.1 %>% mutate(peso_morador_selec=((V00291*(94114/168426190))))
pns2019.1<-pns2019.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2019.1$peso_morador_selec)

## Definição do peso e filtragem de respondentes do questionário

In [ ]:
#Algum tipo de violência nos últimos 12 meses anteriores à pesquisa. - V001P
pns2019.1 <- pns2019.1  %>% mutate(V001P= if_else(V00201 == 1 | V00202 == 1 | V00203 == 1 | V00204 == 1 | V00205 ==1 | 
                                                  V01401 == 1 | V01402 == 1 | V01403 == 1 | V01404 == 1 | V01405 ==1 | 
                                                  V02701 == 1 | V02702 == 1,1,2,missing=2))
pns2019.1$V001P<-factor(pns2019.1$V001P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$V001P)


#Violência verbal nos últimos 12 meses anteriores à pesquisa. - V002P
pns2019.1 <- pns2019.1  %>% mutate(V002P=if_else(V00201 == 1 | V00202  == 1 | V00203 == 1 |V00204 == 1 | V00205==1,1,
                                                 if_else(V00201 >= 1 & V00202  >= 1 & V00203 >= 1 & V00204 >= 1 & V00205>=1,2,2),missing=2))
pns2019.1$V002P<-factor(pns2019.1$V002P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$V002P)



#Violência física nos últimos 12 meses anteriores à pesquisa . - V003P
pns2019.1 <- pns2019.1  %>% mutate(V003P=if_else(V01401 == 1 | V01402 == 1 | V01403 == 1 | V01404 == 1 | V01405 ==1,1,
                                                 if_else(V01401 >= 1 & V01402 >= 1 &V01403 >= 1 & V01404 >= 1 & 
                                                         V01405>=1,2,2),missing=2))
pns2019.1$V003P<-factor(pns2019.1$V003P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$V003P)



#Violência sexual alguma vez na vida . - V005P
pns2019.1 <- pns2019.1  %>% mutate(V005P=if_else(V02801 == 1 | V02802 == 1 | V02701 == 1 | V02702 == 1,1,
                                                 if_else(V01401 >= 1 & V01402 >= 1 &V01403 >= 1 & V01404 >= 1 & V01405>=1,2,2),missing=2))
pns2019.1$V005P<-factor(pns2019.1$V005P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$V005P)

## Definições de abrangências

### Situação urbana ou rural

In [ ]:
#Situação Urbano ou Rural
pns2019.1 <- pns2019.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2019.1$Sit_Urbano_Rural<-factor(pns2019.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2019.1$Sit_Urbano_Rural)

### Sexo

In [ ]:
#Sexo
pns2019.1 <- pns2019.1 %>% rename(Sexo=C006)
pns2019.1$Sexo<-factor(pns2019.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2019.1$Sexo)

### UF

In [ ]:
#Estados - UFs
pns2019.1 <- pns2019.1 %>% rename(Unidades_da_Federacao=V0001)
pns2019.1$Unidades_da_Federacao<-factor(pns2019.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2019.1$Unidades_da_Federacao)

### Grandes Regiões

In [ ]:
#Grandes Regiões
pns2019.1 <- pns2019.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2019.1$GrandesRegioes)

### Capital

In [ ]:
#Capital
pns2019.1<- pns2019.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2019.1$Capital)

### Faixa Etária

In [ ]:
#Faixas Etárias
pns2019.1 <-  pns2019.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(18,30, 45, 60, 75,Inf),
  labels = c("18 a 29 anos","30 a 44 anos","45 a 59 anos","60 a 74 anos","75 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2019.1$faixa_idade) 

### Raça

In [ ]:
#Raça
pns2019.1 <- pns2019.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2, 2, 
                            ifelse(C009==4, 3, 9))))
pns2019.1$Raca<-factor(pns2019.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))
summary(pns2019.1$Raca)

### Renda per capita

In [ ]:
#Rendimento domiciliar per capita
pns2019.1 <- pns2019.1 %>% mutate(rend_per_capita = ifelse(VDF004 %in% 1:2, 1, 
                        ifelse(VDF004%in% 3, 2, 
                        ifelse(VDF004%in% 4, 3,
                        ifelse(VDF004%in% 5, 4,5)))))

pns2019.1$rend_per_capita<-factor(pns2019.1$rend_per_capita, levels=c(1,2,3,4,5), labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM",
                                                                                   "2 até 3 SM","Mais de 3 SM"))
summary(pns2019.1$rend_per_capita)


### Escolaridade

In [ ]:
# Escolaridade
pns2019.1 <- pns2019.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2019.1$gescol<-factor(pns2019.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Fundamental incompleto ou equivalente","Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente","Superior completo"))
summary(pns2019.1$gescol)

## Criando indicadores

### Filtrando base de indicadores

In [ ]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2019Vsurvey<- pns2019.1 %>% select("V0024","UPA_PNS","peso_morador_selec","V001P", "V002P","V003P","V005P" ,
                                     "C008","C009","V0031","Sit_Urbano_Rural","Sexo","Unidades_da_Federacao", "GrandesRegioes",
                                     "faixa_idade", "Raca","rend_per_capita","gescol","Capital")
summary(pns2019Vsurvey)

### Exporta tabela filtrada com os dados específicos - Módulo V 2019

In [ ]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2019Vsurvey, file.path(diretorio_saida, "pns2019Vsurvey.csv"))

### Cria plano amostral complexo

In [ ]:
#survey design
desPNSV=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2019Vsurvey)
desPNSV_18=subset(desPNSV, C008>=18)
desPNSV_C18=subset(desPNSV, C008>=18 & V0031==1)
desPNSV_R18=subset(desPNSV, C008>=18 & !is.na(Raca))

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [ ]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [ ]:
ListaIndicadores = c(~V001P,~V002P,~V003P,~V005P)
ListaIndicadoresTexto = c("V001P","V002P","V003P","V005P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,~Unidades_da_Federacao,~GrandesRegioes,~gescol,~Capital)
ListaDominiosTexto = c("sexo","raça","rend_per_capita","fx_idade_18","urb_rur","uf","região","gescol","capital")
ListaTotais = c('Brasil', 'Capital')
Ano <- "2019"

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [ ]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
#Para cada indicador
for( indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    #Para cada dominio
    for (dominio in ListaDominios){
               #design especifico para capital que é subconjunto do dataframe total
               if (ListaDominiosTexto[j]=="capital"){
                   #designs especificos por variavel que são subconjuntos do dataset total
                     dataframe_indicador<-svyby( indicador , dominio , desPNSV_C18 , svymean,vartype= c("ci", "cv"))
               #Uso design do subconjunto para raça/cor que inclui preta,branca e parda as outras 
               #não possuiam dados suficientes para os dominios dos indicadores
               } else if (ListaDominiosTexto[j]=="raça"){
                   dataframe_indicador<-svyby( indicador , dominio , desPNSV_R18 , svymean,vartype= c("ci", "cv"))
               #design geral para o subconjunto maior que 18 anos
               } else {
                   dataframe_indicador<-svyby( indicador , dominio , desPNSV_18 , svymean,vartype= c("ci", "cv"))
               }
               #União do dataframe de indicadores no formato do painel disponibilizado para PNS
               dataframe_indicador<-data.frame(dataframe_indicador)
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores, dataframe_indicador)
               j <- j + 1
    }
}

#### Criando a tabela pela abrangência total

In [ ]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [ ]:
i=0
for(indicador in ListaIndicadores){
    i <- i+1
    for(total in ListaTotais){
        #Uso do design que é subconjunto do dataset para cada Capital
        if (total == "Capital"){
                   #Indicadores que são subconjunto do dataset tot
                           dataframe_indicador <- svymean(indicador,desPNSV_C18)            
        } else {
                           dataframe_indicador <- svymean(indicador,desPNSV_18)
                }
        
        intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))
        
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
                
        colnames(dataframe_indicador_S) <- c('Sim','LowerS','UpperS', 'cvS')
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                               select('Sim','LowerS','UpperS','cvS')
        dataframe_indicador_S$Indicador <- ListaIndicadoresTexto[i]
        
        dataframe_indicador_S$abr_tipo <- "total"
        dataframe_indicador_S$abr_nome <- total
        dataframe_indicador_S$Ano <- "2019" 
        
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS",'cvS')
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador_S)
        
    }
}
    

#### Unindo tabela de indicadores e de totais

In [ ]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Visualizando tabela de indicadores

In [ ]:
matrizIndicadores

#### Exportando tabela de indicadores calculados - Módulo V 2019

In [ ]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida,"Indicadores_2019V_R.csv"),sep = ";",dec = ",",row.names = FALSE)